<a href="https://colab.research.google.com/github/AhmedMorra1/Coursera_Capstone/blob/master/Toronto_Clustering.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Segmenting and Clustering Neighborhoods in Toronto

Let's import the libraries needed first

In [1]:
#handle arrays
import numpy as np
#handle the data analysis
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
#handle json files
import json
#convert json to dataframes
from pandas.io.json import json_normalize
#handle requests from api and wikipedia
import requests
#handle html pages
from bs4 import BeautifulSoup
#import visualization library
import matplotlib.cm as cm
import matplotlib.colors as colors
#import k means for clustering
from sklearn.cluster import KMeans
#install geopy to get longitude and latitude
#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim 
#install folium map rendering library
#!conda install -c conda-forge folium=0.5.0 --yes
import folium

print("Libraries imported.")

Libraries imported.


Our data is in a table on wikipedia

Let's put that table into a dataframe

In [2]:
df = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')[0]
df.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

Ok, Now let's clean our data and 

1.   remove the Not Assigned Borough  
2.   and replace the Not assigned Neighborhoods with the name of their Borough

In [4]:
#1
for index, row in df.iterrows():
  if row[1] == 'Not assigned':
    df.drop(index,inplace=True)
#2
for index, row in df.iterrows():
  if row[2] == 'Not assigned':
    row[2] = row[1]
df.head()    

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M6A        North York  Lawrence Heights
6      M6A        North York    Lawrence Manor

Great, Now let's add the latitude and longitude of each neighborhood

In [6]:
df2 = pd.read_csv("http://cocl.us/Geospatial_data")
df2.rename(columns={'Postal Code':'Postcode'}, inplace=True)
df.set_index('Postcode')
df2.set_index('Postcode')
tn = pd.merge(df,df2)
tn.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

OK let's put that on a map

In [7]:
address = 'Toronto, Canada'
geolocator = Nominatim(user_agent='to_explore')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('Toronto has latitude of {} and longitude of {}'.format(latitude,longitude))

Toronto has latitude of 43.653963 and longitude of -79.387207


In [9]:
Toronto_map = folium.Map(location=[latitude,longitude])
for lat,lon,borough,neighborhood in zip(tn['Latitude'],tn['Longitude'],tn['Borough'],tn.iloc[:,2]):
    label = '{},{}'.format(neighborhood, borough)
    label = folium.Popup(label,parse_html=True)
    folium.CircleMarker(
        [lat,lon],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=.7,
        parse_html=False).add_to(Toronto_map)
Toronto_map

Now foursqaure API time

In [10]:
CLIENT_ID = 'ABGD1FXT5SO01ODC3IGKVU2LCE1L5ZAX5IUFVZPAKX0RC5PX' # your Foursquare ID
CLIENT_SECRET = 'YKY2JNPHZ3Z2UGTHGDS313PLTNAUYROFMRUYSMENOPHIDHJJ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ABGD1FXT5SO01ODC3IGKVU2LCE1L5ZAX5IUFVZPAKX0RC5PX
CLIENT_SECRET:YKY2JNPHZ3Z2UGTHGDS313PLTNAUYROFMRUYSMENOPHIDHJJ


Now let's get the venues of the toronto neighborhoods

In [0]:
LIMIT = 100
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [15]:
toronto_venues = getNearbyVenues(names=tn.iloc[:,2],
                                   latitudes=tn['Latitude'],
                                   longitudes=tn['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Queen's Park
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toronto 

In [16]:
print(toronto_venues.shape)
toronto_venues.head()

(4372, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [17]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Agincourt                                                              5   
Agincourt North                                                        3   
Albion Gardens                                                         8   
Alderwood                                                              9   
Bathurst Manor                                                        19   
Bathurst Quay                                                         15   
Bayview Village                                                        4   
Beaumond Heights                                                       8   
Bedford Park                                                          23   
Berczy Park                                                           55   
Birch Cliff                                                            4   
Bloordale Gardens                                                      7   
Brockton                                                              22   
Business Reply Mail Processing Centre 969 Eastern                     16   
CFB Toronto                                                            2   
CN Tower                                                              15   
Cabbagetown                                                           43   
Caledonia-Fairbanks                                                    5   
Canada Post Gateway Processing Centre                                 10   
Cedarbrae                                                              8   
Central Bay Street                                                    84   
Chinatown                                                             94   
Christie                                                              17   
Church and Wellesley                                                  83   
Clairlea                                                              10   
Clarks Corners                                                        12   
Cliffcrest                                                             2   
Cliffside                                                              2   
Cliffside West                                                         4   
Cloverdale                                                             2   
Commerce Court                                                       100   
Davisville                                                            35   
Davisville North                                                       9   
Deer Park                                                             15   
Del Ray                                                                4   
Design Exchange                                                      100   
Don Mills North                                                        4   
Don Mills South                                                       21   
Dorset Park                                                            7   
Dovercourt Village                                                    17   
Downsview                                                              3   
Downsview Central                                                      3   
Downsview East                                                         2   
Downsview North                                                       19   
Downsview Northwest                                                    4   
Downsview West                                                         6   
Dufferin                                                              17   
East Birchmount Park                                                   8   
East Toronto                                                           4   
Emery                                                                  2   
Eringate               

In [18]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 272 uniques categories.


In [19]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0                       0            0                    0                 0   
1                       0            0                    0                 0   
2                       0            0                    0                 0   
3                       0            0                    0                 0   
4                       0            0                    0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                   0            0              0          0           0   
1                   0            0              0          0           0   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0                   0          0       0           0              0   
1                   0          0       0           0              0   
2                   0          0       0           0              0   
3                   0          0       0           0              0   
4                   0          0       0           0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0            0                0       

In [20]:
toronto_onehot.shape

(4372, 272)

In [21]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                             Adelaide     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                       Albion Gardens     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                        Bathurst Quay     0.000000   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                   Bloordale Gardens     0.000000   
13                                            Brockton     0.045455   
14   Business Reply Mail Processing Centre 969 Eastern     0.000000   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.000000   
17                                         Cabbagetown     0.000000   
18                                 Caledonia-Fairbanks     0.000000   
19               Canada Post Gateway Processing Centre     0.000000   
20                                           Cedarbrae     0.000000   
21                                  Central Bay Street     0.011905   
22                                           Chinatown     0.000000   
23                                            Christie     0.000000   
24                                Church and Wellesley     0.012048   
25                                            Clairlea     0.000000   
26                                      Clarks Corners     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                      Cliffside West     0.000000   
30                                          Cloverdale     0.000000   
31                                      Commerce Court     0.000000   
32                                          Davisville     0.000000   
33                                    Davisville North     0.000000   
34                                           Deer Park     0.000000   
35                                             Del Ray     0.000000   
36                                     Design Exchange     0.000000   
37                                     Don Mills North     0.000000   
38                                     Don Mills South     0.000000   
39                                         Dorset Park     0.000000   
40                                  Dovercourt Village     0.000000   
41                                           Downsview     0.000000   
42                                   Downsview Central     0.000000   
43                                      Downsview East     0.000000   
44                                     Downsview North     0.000000   
45                                 Downsview Northwest     0.000000   
46                                      Downsview West     0.000000   
47                                            Dufferin     0.000000   
48                                East Birchmount Park     0.000000   
49                                        East Toronto     0.000000   
50                                               Emery     0.000000   
51                                            Eringate     0.000000   
52                                    Exhibition Place     0.045455   
53                                            Fairview     0.000000   
54                                First Canadian Place     0.000000   
55                                     Flemingdon Park     0.00000

In [22]:
toronto_grouped.shape

(206, 272)

In [23]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
             venue  freq
0      Coffee Shop  0.07
1             Café  0.05
2       Steakhouse  0.04
3  Thai Restaurant  0.04
4     Burger Joint  0.03


----Agincourt----
                       venue  freq
0                     Lounge   0.2
1  Latin American Restaurant   0.2
2               Skating Rink   0.2
3             Clothing Store   0.2
4             Breakfast Spot   0.2


----Agincourt North----
                 venue  freq
0                 Park  0.33
1           Playground  0.33
2  Arts & Crafts Store  0.33
3          Yoga Studio  0.00
4          Men's Store  0.00


----Albion Gardens----
                 venue  freq
0        Grocery Store  0.12
1          Video Store  0.12
2           Beer Store  0.12
3       Sandwich Place  0.12
4  Fried Chicken Joint  0.12


----Alderwood----
            venue  freq
0     Pizza Place  0.22
1    Dance Studio  0.11
2  Sandwich Place  0.11
3    Skating Rink  0.11
4             Gym  0.11


----Bathurst Manor----
            ven

Now let's get the top 10 venues for each neighborhood

In [0]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [91]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood      1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide                Coffee Shop                  Café   
1        Agincourt  Latin American Restaurant          Skating Rink   
2  Agincourt North                       Park   Arts & Crafts Store   
3   Albion Gardens                Pizza Place         Grocery Store   
4        Alderwood                Pizza Place           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Thai Restaurant            Steakhouse          Burger Joint   
1        Clothing Store                Lounge        Breakfast Spot   
2            Playground        Discount Store         Deli / Bodega   
3           Video Store            Beer Store              Pharmacy   
4              Pharmacy        Sandwich Place          Dance Studio   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Bar                Bakery            Restaurant   
1      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
2      Department Store          Dessert Shop    Dim Sum Restaurant   
3   Fried Chicken Joint  Fast Food Restaurant        Sandwich Place   
4          Skating Rink                   Pub                   Gym   

  9th Most Common Venue 10th Most Common Venue  
0      Sushi Restaurant       Asian Restaurant  
1                 Diner         Discount Store  
2                 Diner                Dog Run  
3        Discount Store       Department Store  
4  Colombian Restaurant            Curling Ice

Now let's Start Clustering these neighborhoods using k means

In [92]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 3, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [93]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = tn

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on=toronto_merged.iloc[:,2])

# check the last columns!
toronto_merged.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M6A        North York  Lawrence Heights  43.718518 -79.464763   
4      M6A        North York    Lawrence Manor  43.718518 -79.464763   

   Cluster Labels   1st Most Common Venue 2nd Most Common Venue  \
0             3.0                    Park     Food & Drink Shop   
1             0.0       French Restaurant           Coffee Shop   
2             0.0             Coffee Shop                  Park   
3             0.0  Furniture / Home Store        Clothing Store   
4             0.0  Furniture / Home Store        Clothing Store   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0        Discount Store          Deli / Bodega      Department Store   
1          Hockey Arena  Portuguese Restaurant                 Diner   
2                   Pub                 Bakery    Mexican Restaurant   
3    Miscellaneous Shop      Accessories Store              Boutique   
4    Miscellaneous Shop      Accessories Store              Boutique   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Dessert Shop    Dim Sum Restaurant                 Diner   
1           Dance Studio         Deli / Bodega      Department Store   
2                   Café            Restaurant               Theater   
3  Vietnamese Restaurant           Coffee Shop      Fraternity House   
4  Vietnamese Restaurant           Coffee Shop      Fraternity House   

  9th Most Common Venue 10th Most Common Venue  
0               Dog Run   Ethiopian Restaurant  
1          Dessert Shop     Dim Sum Restaurant  
2        Breakfast Spot       Greek Restaurant  
3          Carpet Store          Deli / Bodega  
4          Carpet Store          Deli / Bodega

In [99]:
toronto_merged['Cluster Labels'].unique()

array([ 3.,  0.,  1.,  4., nan,  2.])

In [0]:
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype('object')

In [106]:
toronto_merged['Cluster Labels'].unique()

array([3.0, 0.0, 1.0, 4.0, nan, 2.0], dtype=object)

In [111]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

#set color scheme for the clusters
markers_colors = {0.0:'blue',1.0:'green',2.0:'yellow',3.0:'black',4.0:'pink',toronto_merged['Cluster Labels'].unique()[-2]:'grey'}
c=0
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged.iloc[:,2], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=markers_colors[cluster],
        fill=True,
        fill_color=markers_colors[cluster],
        fill_opacity=0.7).add_to(map_clusters)
    
       
map_clusters

Now let's explore the neighborhoods

In [123]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0.0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]].drop_duplicates()

Borough Cluster Labels      1st Most Common Venue  \
1          North York              0          French Restaurant   
2    Downtown Toronto              0                Coffee Shop   
3          North York              0     Furniture / Home Store   
5        Queen's Park              0                Coffee Shop   
6    Downtown Toronto              0                Coffee Shop   
9          North York              0                       Café   
10          East York              0                Pizza Place   
12   Downtown Toronto              0                Coffee Shop   
14         North York              0                       Park   
20        Scarborough              0                        Bar   
23         North York              0                 Beer Store   
25          East York              0               Dance Studio   
26   Downtown Toronto              0                Coffee Shop   
27               York              0                      Trail   
28          Etobicoke              0                Coffee Shop   
32        Scarborough              0          Electronics Store   
35       East Toronto              0                      Trail   
36   Downtown Toronto              0                Coffee Shop   
38        Scarborough              0                Coffee Shop   
39          East York              0                Coffee Shop   
40   Downtown Toronto              0                Coffee Shop   
41   Downtown Toronto              0                       Café   
42        Scarborough              0                     Bakery   
43         North York              0                Golf Course   
44         North York              0                Coffee Shop   
47          East York              0          Indian Restaurant   
48   Downtown Toronto              0                Coffee Shop   
51       West Toronto              0                Supermarket   
53        Scarborough              0                 Playground   
54         North York              0             Clothing Store   
57         North York              0     Furniture / Home Store   
60   Downtown Toronto              0                Coffee Shop   
63       West Toronto              0                        Bar   
65        Scarborough              0             Discount Store   
68         North York              0         Chinese Restaurant   
71       East Toronto              0           Greek Restaurant   
73   Downtown Toronto              0                Coffee Shop   
75       West Toronto              0                       Café   
78        Scarborough              0                   Bus Line   
81         North York              0                  Cafeteria   
83         North York              0              Grocery Store   
84       East Toronto              0             Sandwich Place   
86   Downtown Toronto              0                Coffee Shop   
91         North York              0        Empanada Restaurant   
92        Scarborough              0                      Motel   
98       East Toronto              0                       Café   
99         North York              0           Sushi Restaurant   
101              York              0                Coffee Shop   
107       Scarborough              0               Skating Rink   
109        North York              0                Coffee Shop   
110        North York              0         Athletics & Sports   
111   Central Toronto              0                       Park   
112   Central Toronto              0                     Garden   
113              York              0              Grocery Store   
114              York              0                Coffee Shop   
116       Scarborough              0          Indian Restaurant   
120   Central Toronto              0                      Hotel   
121   Central Toronto              0                       Park   
123      West Toronto              0         Mexican Restaura

In [122]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1.0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]].drop_duplicates()

Borough Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
7   Scarborough              1  Fast Food Restaurant            Print Shop   
15    Etobicoke              1            Print Shop   Filipino Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
7          Women's Store               Dog Run      Department Store   
15         Women's Store               Dog Run      Department Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
7           Dessert Shop    Dim Sum Restaurant                 Diner   
15          Dessert Shop    Dim Sum Restaurant                 Diner   

   9th Most Common Venue 10th Most Common Venue  
7         Discount Store       Doner Restaurant  
15        Discount Store       Doner Restaurant

In [121]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2.0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]].drop_duplicates()

Borough Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
192  Etobicoke              2                 River                  Pool   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192         Women's Store                 Diner         Deli / Bodega   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192      Department Store          Dessert Shop    Dim Sum Restaurant   

    9th Most Common Venue 10th Most Common Venue  
192        Discount Store            Curling Ice

In [120]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3.0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]].drop_duplicates()

Borough Cluster Labels 1st Most Common Venue  \
0          North York              3                  Park   
37               York              3                  Park   
59          East York              3                  Park   
69         North York              3                  Park   
88         North York              3                  Park   
95         North York              3                  Park   
115              York              3                  Park   
119        North York              3                  Park   
154       Scarborough              3                  Park   
182  Downtown Toronto              3                  Park   

    2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
0       Food & Drink Shop              Discount Store         Deli / Bodega   
37   Fast Food Restaurant                      Market         Women's Store   
59      Convenience Store                 Coffee Shop      Department Store   
69                Airport            Doner Restaurant      Department Store   
88                 Bakery  Construction & Landscaping      Doner Restaurant   
95              Piano Bar              Discount Store          Dance Studio   
115     Convenience Store                     Dog Run      Department Store   
119                  Bank           Convenience Store   Empanada Restaurant   
154   Arts & Crafts Store                  Playground        Discount Store   
182            Playground                       Trail   Dumpling Restaurant   

    5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
0        Department Store                 Dessert Shop    Dim Sum Restaurant   
37         General Travel        General Entertainment   Dumpling Restaurant   
59           Dessert Shop           Dim Sum Restaurant                 Diner   
69           Dessert Shop           Dim Sum Restaurant                 Diner   
88           Dessert Shop           Dim Sum Restaurant                 Diner   
95          Deli / Bodega             Department Store          Dessert Shop   
115          Dessert Shop           Dim Sum Restaurant                 Diner   
119     Electronics Store  Eastern European Restaurant   Dumpling Restaurant   
154         Deli / Bodega             Department Store          Dessert Shop   
182             Drugstore                   Donut Shop      Doner Restaurant   

    8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
0                   Diner                      Dog Run   Ethiopian Restaurant  
37              Drugstore                   Donut Shop              Gift Shop  
59         Discount Store                      Dog Run          Women's Store  
69         Discount Store                      Dog Run             Donut Shop  
88         Discount Store                      Dog Run             Donut Shop  
95     Dim Sum Restaurant                        Diner          Women's Store  
115        Discount Store             Doner Restaurant           Dance Studio  
119             Drugstore                   Donut Shop          Deli / Bodega  
154    Dim Sum Restaurant                        Diner                Dog Run  
182               Dog Run  Eastern European Restaurant           Cupcake Shop

In [119]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4.0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]].drop_duplicates()

Borough Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
97   North York              4        Baseball Field              Food Truck   
105  North York              4        Baseball Field  Furniture / Home Store   
197   Etobicoke              4        Baseball Field                    Pool   

    3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
97       Business Service         Women's Store                 Dessert Shop   
105          Dance Studio      Department Store                 Dessert Shop   
197      Business Service     Electronics Store  Eastern European Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
97     Dim Sum Restaurant                 Diner        Discount Store   
105    Dim Sum Restaurant                 Diner        Discount Store   
197   Dumpling Restaurant             Drugstore            Donut Shop   

    9th Most Common Venue 10th Most Common Venue  
97                Dog Run       Doner Restaurant  
105               Dog Run          Women's Store  
197      Doner Restaurant          Deli / Bodega